In [1]:
# notebook pour implementer l'analyse de fourier pour créer de nouvelles variables explicatives

In [118]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.pyplot import figure
from datetime import datetime

from numpy.fft import fft 
from numpy import pi, cos, sin 

from scipy.signal import find_peaks

from sklearn.linear_model import LinearRegression

from tqdm import tqdm

In [6]:
df_sy = pd.read_csv("../../data/sales_train_validation.csv")

df4=df_sy.drop(columns=['cat_id','store_id','state_id','item_id','dept_id'])
df4

id  d_1  d_2  d_3  d_4  d_5  d_6  d_7  d_8  \
0      HOBBIES_1_001_CA_1_validation    0    0    0    0    0    0    0    0   
1      HOBBIES_1_002_CA_1_validation    0    0    0    0    0    0    0    0   
2      HOBBIES_1_003_CA_1_validation    0    0    0    0    0    0    0    0   
3      HOBBIES_1_004_CA_1_validation    0    0    0    0    0    0    0    0   
4      HOBBIES_1_005_CA_1_validation    0    0    0    0    0    0    0    0   
...                              ...  ...  ...  ...  ...  ...  ...  ...  ...   
30485    FOODS_3_823_WI_3_validation    0    0    2    2    0    3    1    4   
30486    FOODS_3_824_WI_3_validation    0    0    0    0    0    5    0    1   
30487    FOODS_3_825_WI_3_validation    0    6    0    2    2    4    1    8   
30488    FOODS_3_826_WI_3_validation    0    0    0    0    0    0    0    0   
30489    FOODS_3_827_WI_3_validation    0    0    0    0    0    0    0    0   

       d_9  ...  d_1904  d_1905  d_1906  d_1907  d_1908  d_1909  d_1910  \
0        0  ...       1       3       0       1       1       1       3   
1        0  ...       0       0       0       0       0       1       0   
2        0  ...       2       1       2       1       1       1       0   
3        0  ...       1       0       5       4       1       0       1   
4        0  ...       2       1       1       0       1       1       2   
...    ...  ...     ...     ...     ...     ...     ...     ...     ...   
30485    1  ...       2       0       0       0       0       0       1   
30486    1  ...       0       0       0       0       0       0       0   
30487    5  ...       2       1       0       2       0       1       0   
30488    0  ...       0       0       1       0       0       1       0   
30489    0  ...       0       0       0       0       0       0       0   

       d_1911  d_1912  d_1913  
0           0       1       1  
1           0       0       0  
2           1       1       1  
3           3       7       2  
4           2       2       4  
...       ...     ...     ...  
30485       0       0       1  
30486       0       1       0  
30487       0       1       0  
30488       3       1       3  
30489       0       0       0  

[30490 rows x 1914 columns]

In [139]:
df_test = df4.sample(3)
df_test

id  d_1  d_2  d_3  d_4  d_5  d_6  d_7  \
18448    HOBBIES_1_159_TX_3_validation    1    0    0    0    0    0    0   
24765    HOBBIES_1_382_WI_2_validation    0    0    0    0    0    0    0   
25363  HOUSEHOLD_1_416_WI_2_validation    0    0    0    0    0    0    0   

       d_8  d_9  ...  d_1904  d_1905  d_1906  d_1907  d_1908  d_1909  d_1910  \
18448    0    0  ...       0       0       0       0       0       0       0   
24765    0    0  ...       0       0       1       0       1       0       1   
25363    0    0  ...       1       3       0       0       0       1       3   

       d_1911  d_1912  d_1913  
18448       0       0       0  
24765       0       2       0  
25363       2       0       0  

[3 rows x 1914 columns]

In [140]:
df_test_slice = df_test.set_index('id')
df_test_slice = df_test_slice.loc[:, 'd_1548':]
df_test_slice

d_1548  d_1549  d_1550  d_1551  d_1552  \
id                                                                        
HOBBIES_1_159_TX_3_validation         0       1       0       0       0   
HOBBIES_1_382_WI_2_validation         0       0       0       0       0   
HOUSEHOLD_1_416_WI_2_validation       0       2       0       3       0   

                                 d_1553  d_1554  d_1555  d_1556  d_1557  ...  \
id                                                                       ...   
HOBBIES_1_159_TX_3_validation         0       0       0       0       0  ...   
HOBBIES_1_382_WI_2_validation         0       0       0       0       0  ...   
HOUSEHOLD_1_416_WI_2_validation       4       4       1       0       0  ...   

                                 d_1904  d_1905  d_1906  d_1907  d_1908  \
id                                                                        
HOBBIES_1_159_TX_3_validation         0       0       0       0       0   
HOBBIES_1_382_WI_2_validation         0       0       1       0       1   
HOUSEHOLD_1_416_WI_2_validation       1       3       0       0       0   

                                 d_1909  d_1910  d_1911  d_1912  d_1913  
id                                                                       
HOBBIES_1_159_TX_3_validation         0       0       0       0       0  
HOBBIES_1_382_WI_2_validation         0       1       0       2       0  
HOUSEHOLD_1_416_WI_2_validation       1       3       2       0       0  

[3 rows x 366 columns]

In [117]:
df4_slice = df4.set_index('id')
df4_slice = df4_slice.loc[:, 'd_1548':]
df4_slice

d_1548  d_1549  d_1550  d_1551  d_1552  d_1553  \
id                                                                              
HOBBIES_1_001_CA_1_validation       2       0       1       0       0       0   
HOBBIES_1_002_CA_1_validation       0       0       1       0       0       0   
HOBBIES_1_003_CA_1_validation       0       0       0       0       0       1   
HOBBIES_1_004_CA_1_validation       2       3       0       2       1       2   
HOBBIES_1_005_CA_1_validation       2       0       2       1       2       0   
...                               ...     ...     ...     ...     ...     ...   
FOODS_3_823_WI_3_validation         0       0       0       0       0       0   
FOODS_3_824_WI_3_validation         0       0       0       0       0       0   
FOODS_3_825_WI_3_validation         0       1       1       2       1       1   
FOODS_3_826_WI_3_validation         0       0       0       0       0       0   
FOODS_3_827_WI_3_validation         1       0       2       4       0       0   

                               d_1554  d_1555  d_1556  d_1557  ...  d_1904  \
id                                                             ...           
HOBBIES_1_001_CA_1_validation       1       1       2       0  ...       1   
HOBBIES_1_002_CA_1_validation       0       0       1       0  ...       0   
HOBBIES_1_003_CA_1_validation       0       1       0       0  ...       2   
HOBBIES_1_004_CA_1_validation       1       6       7       0  ...       1   
HOBBIES_1_005_CA_1_validation       2       3       4       2  ...       2   
...                               ...     ...     ...     ...  ...     ...   
FOODS_3_823_WI_3_validation         0       0       0       0  ...       2   
FOODS_3_824_WI_3_validation         0       0       0       0  ...       0   
FOODS_3_825_WI_3_validation         0       2       1       3  ...       2   
FOODS_3_826_WI_3_validation         0       0       0       0  ...       0   
FOODS_3_827_WI_3_validation         0       5      10       5  ...       0   

                               d_1905  d_1906  d_1907  d_1908  d_1909  d_1910  \
id                                                                              
HOBBIES_1_001_CA_1_validation       3       0       1       1       1       3   
HOBBIES_1_002_CA_1_validation       0       0       0       0       1       0   
HOBBIES_1_003_CA_1_validation       1       2       1       1       1       0   
HOBBIES_1_004_CA_1_validation       0       5       4       1       0       1   
HOBBIES_1_005_CA_1_validation       1       1       0       1       1       2   
...                               ...     ...     ...     ...     ...     ...   
FOODS_3_823_WI_3_validation         0       0       0       0       0       1   
FOODS_3_824_WI_3_validation         0       0       0       0       0       0   
FOODS_3_825_WI_3_validation         1       0       2       0       1       0   
FOODS_3_826_WI_3_validation         0       1       0       0       1       0   
FOODS_3_827_WI_3_validation         0       0       0       0       0       0   

                               d_1911  d_1912  d_1913  
id                                                     
HOBBIES_1_001_CA_1_validation       0       1       1  
HOBBIES_1_002_CA_1_validation       0       0       0  
HOBBIES_1_003_CA_1_validation       1       1       1  
HOBBIES_1_004_CA_1_validation       3       7       2  
HOBBIES_1_005_CA_1_validation       2       2       4  
...                               ...     ...     ...  
FOODS_3_823_WI_3_validation         0       0       1  
FOODS_3_824_WI_3_validation         0       1       0  
FOODS_3_825_WI_3_validation         0       1       0  
FOODS_3_826_WI_3_validation         3       1       3  
FOODS_3_827_WI_3_validation         0       0       0  

[30490 rows x 366 columns]

In [155]:
for index, row in df4.iterrows():
    df_row = pd.DataFrame(row)
    
    df_row = df_row.T
    

    df_row = pd.melt(df_row,id_vars = 'id',
                  value_vars = [col for col in df_row.columns if col.startswith("d_")],
                  var_name = "d",
                  value_name = "sales")
    
    df_row['sales'] = df_row['sales'].astype('int32')
    
    df_row_1547 = df_row.iloc[1547:]
    #print(df_row_1547)
    
    
    x = df_row_1547['sales']
   #print(x)
    M = len(x)
    xf = fft(x,M)
    f = np.arange(M)/M
    
    tempo = (np.abs(xf)).tolist()
    maximum = max(tempo)
    tempo.remove(maximum)
    #print(tempo)
    new_max = max(tempo)
    #print(new_max)
    #peaks = find_peaks(np.abs(xf), height=new_max/3, distance=30)
    
    if index > 0:
        peaks = find_peaks(np.abs(xf), height=new_max/3, distance=30)
    else:
        peaks = find_peaks(np.abs(xf), height=new_max/3, distance=30)
        
        
    reg = LinearRegression()

    t = np.arange(1547,1913)
    print("peaks[0] = {}".format(peaks[0]))
    loop = int(len(peaks[0])/2)
    print("nb de tour de boucle = {}".format(loop))
    
    if loop==0:
        pass
    
    else:

        list_ff = list()

        for i in range(0,loop):
            ff = peaks[0][i] / M
            list_ff.append(ff)
        print("list de transformée = {}".format(list_ff))
        dict_X = {}

        for index, item in enumerate(list_ff):
            keyc= "x{}c".format(index)
            keys = "x{}s".format(index)

            cos_x = cos(2*pi*item*t)
            sin_x = sin(2*pi*item*t)

            dict_X[keyc] = cos_x
            dict_X[keys] = sin_x

        X = pd.DataFrame(dict_X)

        reg.fit(X,x)
        xx = reg.predict(X)
        xx = np.abs(xx)
        df_xx = pd.DataFrame(xx)

        day = x.index.values
        df_xx['d'] = df_row_1547['d'].values
        df_xx['id'] = row['id']


        df_xx = df_xx.rename(columns={0:'sales'})
        df_pivot = df_xx.pivot(index='id', columns='d', values='sales')
        df4_slice = df_pivot.combine_first(df4_slice)
        #print(df4_slice)

    

peaks[0] = [  2  43  83 143 179 223 283 323 364]
nb de tour de boucle = 4
list de transformée = [0.00546448087431694, 0.11748633879781421, 0.226775956284153, 0.3907103825136612]
peaks[0] = [  3  59  93 134 166 200 232 273 307 363]
nb de tour de boucle = 5
list de transformée = [0.00819672131147541, 0.16120218579234974, 0.2540983606557377, 0.366120218579235, 0.453551912568306]
peaks[0] = [  4  52  88 147 183 219 278 314 362]
nb de tour de boucle = 4
list de transformée = [0.01092896174863388, 0.14207650273224043, 0.24043715846994534, 0.4016393442622951]
peaks[0] = [ 52 104 134 165 201 232 262 314]
nb de tour de boucle = 4
list de transformée = [0.14207650273224043, 0.28415300546448086, 0.366120218579235, 0.45081967213114754]
peaks[0] = [  9  46  78 108 162 204 258 288 320 357]
nb de tour de boucle = 5
list de transformée = [0.02459016393442623, 0.12568306010928962, 0.21311475409836064, 0.29508196721311475, 0.4426229508196721]
peaks[0] = [  6  52  83 125 168 198 241 283 314 360]
nb de to

peaks[0] = [ 12  66 124 183 242 300 354]
nb de tour de boucle = 3
list de transformée = [0.03278688524590164, 0.18032786885245902, 0.33879781420765026]
peaks[0] = [  8  60  92 140 170 226 274 306 358]
nb de tour de boucle = 4
list de transformée = [0.02185792349726776, 0.16393442622950818, 0.25136612021857924, 0.3825136612021858]
peaks[0] = [  2  32  63  99 141 171 225 267 303 334 364]
nb de tour de boucle = 5
list de transformée = [0.00546448087431694, 0.08743169398907104, 0.1721311475409836, 0.27049180327868855, 0.38524590163934425]
peaks[0] = [ 14  52 112 144 177 222 254 314 352]
nb de tour de boucle = 4
list de transformée = [0.03825136612021858, 0.14207650273224043, 0.30601092896174864, 0.39344262295081966]
peaks[0] = [  9  52 101 149 181 217 265 314 357]
nb de tour de boucle = 4
list de transformée = [0.02459016393442623, 0.14207650273224043, 0.27595628415300544, 0.40710382513661203]
peaks[0] = [  7  52  99 133 166 200 233 267 314 359]
nb de tour de boucle = 5
list de transformée

peaks[0] = [ 17  53 101 139 184 227 265 313 349]
nb de tour de boucle = 4
list de transformée = [0.04644808743169399, 0.1448087431693989, 0.27595628415300544, 0.3797814207650273]
peaks[0] = [ 17  52 105 157 209 261 314 349]
nb de tour de boucle = 4
list de transformée = [0.04644808743169399, 0.14207650273224043, 0.28688524590163933, 0.42896174863387976]
peaks[0] = [  6  55  94 128 158 208 238 272 311 360]
nb de tour de boucle = 5
list de transformée = [0.01639344262295082, 0.15027322404371585, 0.2568306010928962, 0.34972677595628415, 0.43169398907103823]
peaks[0] = [  3  33  96 158 208 270 333 363]
nb de tour de boucle = 4
list de transformée = [0.00819672131147541, 0.09016393442622951, 0.26229508196721313, 0.43169398907103823]
peaks[0] = [ 17  58  91 123 157 209 243 275 308 349]
nb de tour de boucle = 5
list de transformée = [0.04644808743169399, 0.15846994535519127, 0.24863387978142076, 0.3360655737704918, 0.42896174863387976]
peaks[0] = [  2  35  72 126 166 200 240 294 331 364]
nb d

peaks[0] = [ 16  54 101 155 211 265 312 350]
nb de tour de boucle = 4
list de transformée = [0.04371584699453552, 0.14754098360655737, 0.27595628415300544, 0.42349726775956287]
peaks[0] = [  8  48  78 115 164 202 251 288 318 358]
nb de tour de boucle = 5
list de transformée = [0.02185792349726776, 0.13114754098360656, 0.21311475409836064, 0.31420765027322406, 0.44808743169398907]
peaks[0] = [  9  52  87 123 183 243 279 314 357]
nb de tour de boucle = 4
list de transformée = [0.02459016393442623, 0.14207650273224043, 0.23770491803278687, 0.3360655737704918]
peaks[0] = [  9  52  85 119 152 183 214 247 281 314 357]
nb de tour de boucle = 5
list de transformée = [0.02459016393442623, 0.14207650273224043, 0.23224043715846995, 0.3251366120218579, 0.41530054644808745]
peaks[0] = [  3  52 104 142 178 224 262 314 363]
nb de tour de boucle = 4
list de transformée = [0.00819672131147541, 0.14207650273224043, 0.28415300546448086, 0.3879781420765027]
peaks[0] = [ 10  42  92 131 164 202 235 274 324 

peaks[0] = [ 11  45  79 130 162 204 236 287 321 355]
nb de tour de boucle = 5
list de transformée = [0.030054644808743168, 0.12295081967213115, 0.21584699453551912, 0.3551912568306011, 0.4426229508196721]
peaks[0] = [  8  39  69 108 139 192 227 258 297 327 358]
nb de tour de boucle = 5
list de transformée = [0.02185792349726776, 0.10655737704918032, 0.1885245901639344, 0.29508196721311475, 0.3797814207650273]
peaks[0] = [  2  53  86 124 166 200 242 280 313 364]
nb de tour de boucle = 5
list de transformée = [0.00546448087431694, 0.1448087431693989, 0.23497267759562843, 0.33879781420765026, 0.453551912568306]
peaks[0] = [  5  37  70 101 156 210 265 296 329 361]
nb de tour de boucle = 5
list de transformée = [0.01366120218579235, 0.10109289617486339, 0.1912568306010929, 0.27595628415300544, 0.4262295081967213]
peaks[0] = [  2  57  95 157 209 271 309 364]
nb de tour de boucle = 4
list de transformée = [0.00546448087431694, 0.1557377049180328, 0.25956284153005466, 0.42896174863387976]
peak

...

peaks[0] = [ 12  52  83 130 162 204 236 283 314 354]
nb de tour de boucle = 5
list de transformée = [0.03278688524590164, 0.14207650273224043, 0.226775956284153, 0.3551912568306011, 0.4426229508196721]
peaks[0] = [  3 363]
nb de tour de boucle = 1
list de transformée = [0.00819672131147541]
peaks[0] = [  4  57  93 124 163 203 242 273 309 362]
nb de tour de boucle = 5
list de transformée = [0.01092896174863388, 0.1557377049180328, 0.2540983606557377, 0.33879781420765026, 0.4453551912568306]
peaks[0] = [  5  38  68 120 158 193 246 298 328 361]
nb de tour de boucle = 5
list de transformée = [0.01366120218579235, 0.10382513661202186, 0.18579234972677597, 0.32786885245901637, 0.43169398907103823]
peaks[0] = [ 11  63 107 154 212 259 303 355]
nb de tour de boucle = 4
list de transformée = [0.030054644808743168, 0.1721311475409836, 0.2923497267759563, 0.4207650273224044]
peaks[0] = [  3  61  91 122 152 182 214 244 275 305 363]
nb de tour de boucle = 5
list de transformée = [0.00819672131147541

peaks[0] = [ 22  61 123 175 243 305 344]
nb de tour de boucle = 3
list de transformée = [0.060109289617486336, 0.16666666666666666, 0.3360655737704918]
peaks[0] = [ 11  52  86 121 173 212 245 280 314 355]
nb de tour de boucle = 5
list de transformée = [0.030054644808743168, 0.14207650273224043, 0.23497267759562843, 0.33060109289617484, 0.4726775956284153]
peaks[0] = [  6  52  90 130 186 236 276 314 360]
nb de tour de boucle = 4
list de transformée = [0.01639344262295082, 0.14207650273224043, 0.2459016393442623, 0.3551912568306011]
peaks[0] = [  2  52 112 153 213 254 314 364]
nb de tour de boucle = 4
list de transformée = [0.00546448087431694, 0.14207650273224043, 0.30601092896174864, 0.4180327868852459]
peaks[0] = [  2  49  81 138 173 228 285 317 364]
nb de tour de boucle = 4
list de transformée = [0.00546448087431694, 0.13387978142076504, 0.22131147540983606, 0.3770491803278688]
peaks[0] = [ 34  65  96 133 191 233 270 301 332]
nb de tour de boucle = 4
list de transformée = [0.09289617

peaks[0] = [  2  48  84 116 148 179 218 250 282 318 364]
nb de tour de boucle = 5
list de transformée = [0.00546448087431694, 0.13114754098360656, 0.22950819672131148, 0.31693989071038253, 0.40437158469945356]
peaks[0] = [ 19  52  86 146 191 232 280 314 347]
nb de tour de boucle = 4
list de transformée = [0.05191256830601093, 0.14207650273224043, 0.23497267759562843, 0.3989071038251366]
peaks[0] = [  6  52  94 146 196 228 272 314 360]
nb de tour de boucle = 4
list de transformée = [0.01639344262295082, 0.14207650273224043, 0.2568306010928962, 0.3989071038251366]
peaks[0] = [ 12  72 119 149 190 247 294 354]
nb de tour de boucle = 4
list de transformée = [0.03278688524590164, 0.19672131147540983, 0.3251366120218579, 0.40710382513661203]
peaks[0] = [ 12  48  81 115 145 183 221 251 285 318 354]
nb de tour de boucle = 5
list de transformée = [0.03278688524590164, 0.13114754098360656, 0.22131147540983606, 0.31420765027322406, 0.39617486338797814]
peaks[0] = [  2  52 314 364]
nb de tour de bo

peaks[0] = [  2  76 138 168 198 228 290 364]
nb de tour de boucle = 4
list de transformée = [0.00546448087431694, 0.20765027322404372, 0.3770491803278688, 0.45901639344262296]
peaks[0] = [  3  52 105 261 314 363]
nb de tour de boucle = 3
list de transformée = [0.00819672131147541, 0.14207650273224043, 0.28688524590163933]
peaks[0] = [ 12  50  80 117 151 183 215 249 286 316 354]
nb de tour de boucle = 5
list de transformée = [0.03278688524590164, 0.1366120218579235, 0.2185792349726776, 0.319672131147541, 0.412568306010929]
peaks[0] = [  3  37  68 102 139 170 227 264 298 329 363]
nb de tour de boucle = 5
list de transformée = [0.00819672131147541, 0.10109289617486339, 0.18579234972677597, 0.2786885245901639, 0.3797814207650273]
peaks[0] = [ 18  57 114 166 200 252 309 348]
nb de tour de boucle = 4
list de transformée = [0.04918032786885246, 0.1557377049180328, 0.3114754098360656, 0.453551912568306]
peaks[0] = [  2  53  95 125 185 241 271 313 364]
nb de tour de boucle = 4
list de transform

peaks[0] = [  5  52 109 141 187 225 257 314 361]
nb de tour de boucle = 4
list de transformée = [0.01366120218579235, 0.14207650273224043, 0.2978142076502732, 0.38524590163934425]
peaks[0] = [  3  52  83 147 179 219 283 314 363]
nb de tour de boucle = 4
list de transformée = [0.00819672131147541, 0.14207650273224043, 0.226775956284153, 0.4016393442622951]
peaks[0] = [ 18  51  88 140 186 226 278 315 348]
nb de tour de boucle = 4
list de transformée = [0.04918032786885246, 0.13934426229508196, 0.24043715846994534, 0.3825136612021858]
peaks[0] = [ 54 136 230 312]
nb de tour de boucle = 2
list de transformée = [0.14754098360655737, 0.37158469945355194]
peaks[0] = [ 12  54  94 181 272 312 354]
nb de tour de boucle = 3
list de transformée = [0.03278688524590164, 0.14754098360655737, 0.2568306010928962]
peaks[0] = [ 11  52 183 314 355]
nb de tour de boucle = 2
list de transformée = [0.030054644808743168, 0.14207650273224043]
peaks[0] = [  5  36  92 136 183 230 274 330 361]
nb de tour de boucl

In [156]:
df4_slice

d_1548    d_1549    d_1550    d_1551  \
id                                                                        
FOODS_1_001_CA_1_validation      0.674633  0.737291  0.523595  0.589511   
FOODS_1_001_CA_2_validation      1.588128  0.733491  0.123893  1.365974   
FOODS_1_001_CA_3_validation      1.958086  0.767862  0.686620  0.654127   
FOODS_1_001_CA_4_validation      0.395325  0.220562  0.139595  0.384551   
FOODS_1_001_TX_1_validation      0.057722  0.041872  0.186977  1.129886   
...                                   ...       ...       ...       ...   
HOUSEHOLD_2_516_TX_2_validation  0.246105  0.461133  0.497872  0.350600   
HOUSEHOLD_2_516_TX_3_validation  0.098045  0.119822  0.010789  0.230448   
HOUSEHOLD_2_516_WI_1_validation  0.004875  0.152489  0.087394  0.062160   
HOUSEHOLD_2_516_WI_2_validation  0.080768  0.086026  0.016704  0.165577   
HOUSEHOLD_2_516_WI_3_validation  0.015379  0.212792  0.312338  0.117113   

                                   d_1552    d_1553    d_1554    d_1555  \
id                                                                        
FOODS_1_001_CA_1_validation      0.530512  0.139542  0.563851  0.675903   
FOODS_1_001_CA_2_validation      1.219625  0.844823  1.081791  0.549487   
FOODS_1_001_CA_3_validation      1.776228  1.931919  0.975390  2.129279   
FOODS_1_001_CA_4_validation      0.258299  0.304940  0.426002  0.205262   
FOODS_1_001_TX_1_validation      0.927472  0.000002  0.792661  0.493181   
...                                   ...       ...       ...       ...   
HOUSEHOLD_2_516_TX_2_validation  0.222434  0.551000  0.174454  0.392321   
HOUSEHOLD_2_516_TX_3_validation  0.149759  0.445187  0.111757  0.136390   
HOUSEHOLD_2_516_WI_1_validation  0.036468  0.049736  0.112129  0.052915   
HOUSEHOLD_2_516_WI_2_validation  0.110126  0.074990  0.031743  0.083570   
HOUSEHOLD_2_516_WI_3_validation  0.198261  0.094819  0.013297  0.034201   

                                   d_1556    d_1557  ...    d_1904    d_1905  \
id                                                   ...                       
FOODS_1_001_CA_1_validation      0.295615  0.833246  ...  0.522082  0.649667   
FOODS_1_001_CA_2_validation      0.690712  0.416591  ...  0.989406  1.035258   
FOODS_1_001_CA_3_validation      1.621855  0.029826  ...  0.130168  1.055270   
FOODS_1_001_CA_4_validation      0.144646  0.243818  ...  0.305422  0.557659   
FOODS_1_001_TX_1_validation      0.246220  0.256260  ...  0.157232  0.334654   
...                                   ...       ...  ...       ...       ...   
HOUSEHOLD_2_516_TX_2_validation  0.693459  0.342744  ...  0.169517  0.335265   
HOUSEHOLD_2_516_TX_3_validation  0.283040  0.105612  ...  0.056868  0.020235   
HOUSEHOLD_2_516_WI_1_validation  0.048651  0.113620  ...  0.060341  0.135400   
HOUSEHOLD_2_516_WI_2_validation  0.027942  0.019626  ...  0.157447  0.002025   
HOUSEHOLD_2_516_WI_3_validation  0.079316  0.214177  ...  0.147356  0.319878   

                                   d_1906    d_1907    d_1908    d_1909  \
id                                                                        
FOODS_1_001_CA_1_validation      0.632877  1.072808  0.950150  0.314333   
FOODS_1_001_CA_2_validation      2.069586  1.170895  0.475853  1.282107   
FOODS_1_001_CA_3_validation      1.361907  1.266157  0.705037  0.366896   
FOODS_1_001_CA_4_validation      0.304791  0.622486  0.276241  0.216536   
FOODS_1_001_TX_1_validation      0.292669  0.999014  0.418376  0.200649   
...                                   ...       ...       ...       ...   
HOUSEHOLD_2_516_TX_2_validation  0.205787  0.260111  0.205026  0.514255   
HOUSEHOLD_2_516_TX_3_validation  0.265230  0.082240  0.195459  0.183211   
HOUSEHOLD_2_516_WI_1_validation  0.064942  0.053353  0.040625  0.075200   
HOUSEHOLD_2_516_WI_2_validation  0.038471  0.023392  0.083987  0.006461   
HOUSEHOLD_2_516_WI_3_validation  0.200836  0.038206  0.163278  0.009371   

                                   d_1910    d_1911    d_1912    d

In [157]:
df4_slice.to_csv('../../fourier_each_item.csv')